In [2]:
import json
import gmaps
from matplotlib import pyplot as plt
import folium
import pandas as pd
import numpy as np
import geopy.distance
from ast import literal_eval
from tqdm import tqdm

/Users/abhishekvasu/Documents/workspace/travel_app_backend/.backpack_env/lib/python3.9/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [4]:
with open("../data/distance_between_cities.json", "r") as f:
    data = json.load(f)
    f.close()

In [4]:
df = pd.read_csv("../data/backpacking_cities_processed.csv")

In [5]:
def decode_polyline(polyline_str):
    '''Pass a Google Maps encoded polyline string; returns list of lat/lon pairs'''
    index, lat, lng = 0, 0, 0
    coordinates = []
    changes = {'latitude': 0, 'longitude': 0}

    # Coordinates have variable length when encoded, so just keep
    # track of whether we've hit the end of the string. In each
    # while loop iteration, a single coordinate is decoded.
    while index < len(polyline_str):
        # Gather lat/lon changes, store them in a dictionary to apply them later
        for unit in ['latitude', 'longitude']: 
            shift, result = 0, 0

            while True:
                byte = ord(polyline_str[index]) - 63
                index += 1
                result |= (byte & 0x1f) << shift
                shift += 5
                if not byte >= 0x20:
                    break

            if (result & 1):
                changes[unit] = ~(result >> 1)
            else:
                changes[unit] = (result >> 1)

        lat += changes['latitude']
        lng += changes['longitude']

        coordinates.append((lat / 100000.0, lng / 100000.0))

    return coordinates

In [7]:
decode_polyline(data[0]['driving_leg'][0]['steps'][4]['polyline']['points'])

[(19.40313, -99.13666),
 (19.40309, -99.13671),
 (19.40304, -99.13678),
 (19.40301, -99.13682),
 (19.403, -99.13684),
 (19.40299, -99.13686),
 (19.40299, -99.13689),
 (19.40299, -99.13692),
 (19.403, -99.13695),
 (19.40301, -99.13699),
 (19.40302, -99.13701),
 (19.40303, -99.13702),
 (19.40305, -99.13705),
 (19.40306, -99.13706),
 (19.40308, -99.13707),
 (19.4031, -99.13708),
 (19.40312, -99.13709),
 (19.40314, -99.1371),
 (19.40317, -99.1371),
 (19.40321, -99.13709),
 (19.40323, -99.13709),
 (19.40324, -99.13708),
 (19.40326, -99.13707),
 (19.40327, -99.13707),
 (19.40327, -99.13706),
 (19.40328, -99.13705),
 (19.40329, -99.13704),
 (19.40329, -99.13703),
 (19.4033, -99.13701),
 (19.40331, -99.13697),
 (19.40332, -99.13689),
 (19.40334, -99.13684),
 (19.40334, -99.13682),
 (19.40336, -99.13679)]

In [ ]:
locations = []

for loc_data in data[0]['driving_leg'][0]['steps']:
    locations.extend(decode_polyline(loc_data['polyline']['points']))

In [ ]:
len(locations)

In [ ]:
gmaps.configure(api_key=gmaps_api_key)

In [ ]:
m = folium.Map(location=locations[0], zoom_start=11)

folium.PolyLine(locations, tooltip="Coast").add_to(m)

m

## Think about TSM

In [8]:
mx_data = list(filter(lambda x: ("Mexico" in x['city_1']) & ("Mexico" in x['city_2']), data))

In [9]:
def get_distance(data_json):

    cities_dist = {}
    
    for data_item in data_json:
    
        city_item_1 = data_item['city_1']
        city_item_2 = data_item['city_2']
    
        try:
            driving_dist = float(data_item['driving_leg'][0]['distance']['text'].split(" ")[0].replace(",", ""))
        except IndexError:
            driving_dist = np.inf
    
        keyname = (city_item_1, city_item_2)
    
        cities_dist[keyname] = driving_dist

    return cities_dist


def create_distance_matrix(cities_dist):

    distance_matrix = []
    distance_matrix_order = []

    all_cities = []
    for city_name in list(cities_dist.keys()):
        all_cities.extend(city_name)

    all_cities = list(set(all_cities))
    
    for city_name_1 in all_cities:
        sub_distance_matrix = []
        for city_name_2 in all_cities:
            if city_name_1 == city_name_2:
                dist = 0
            else:
                try:
                    dist = cities_dist[(city_name_1, city_name_2)]
                except KeyError:
                    dist = cities_dist[(city_name_2, city_name_1)]
    
            sub_distance_matrix.append(dist)
        distance_matrix.append(sub_distance_matrix)
        distance_matrix_order.append(city_name_1)

    return distance_matrix, distance_matrix_order

In [10]:
def insert_distance(distance_matrix, distance_matrix_order, city_1, city_2):

    coords_1 = literal_eval(df[df["query_term"] == city_1]["coord"].values[0])
    coords_2 = literal_eval(df[df["query_term"] == city_2]["coord"].values[0])

    dist = geopy.distance.geodesic(coords_1, coords_2).km

    idx_1 = distance_matrix_order.index(city_1)
    idx_2 = distance_matrix_order.index(city_2)

    distance_matrix[idx_1][idx_2] = dist
    distance_matrix[idx_2][idx_1] = dist

    return None

In [11]:
mx_driving_distance = get_distance(mx_data)

In [22]:
driving_distance = get_distance(data)
# distance_matrix, distance_matrix_order = create_distance_matrix(driving_distance)

In [ ]:
insert_distance(distance_matrix, distance_matrix_order, "Roatan, Honduras", "Utila, Honduras")
insert_distance(distance_matrix, distance_matrix_order, "Roatan, Honduras", "Copan Ruinas, Honduras")
insert_distance(distance_matrix, distance_matrix_order, "Roatan, Honduras", "Caye Caulker, Belize")
insert_distance(distance_matrix, distance_matrix_order, "Corn islands, Nicaragua", "Managua, Nicaragua")
insert_distance(distance_matrix, distance_matrix_order, "Holbox, Mexico", "Cancun, Mexico")

In [ ]:
floydWarshall_dist = floydWarshall(distance_matrix)

In [ ]:
for dist_idx, dist_row in enumerate(distance_matrix):
    if len(set(dist_row)) == 2:
        print(dist_idx)
        print(distance_matrix_order[dist_idx])

In [ ]:
subset_cities = list(filter(lambda x:("Nicaragua" in x) | ("Nicaragua" in x), cities_list))

In [ ]:
# Nearest Neighbor Algorithm function
def nearest_neighbor(distances, starting_city):
    
    cities = list(set(city for cities in distances.keys() for city in cities))

    n = len(cities)

    visited = [False] * n
    path = []
    total_distance = 0.0

    starting_idx = cities.index(starting_city)
    cities[0], cities[starting_idx] = cities[starting_idx], cities[0]

    # Start from the first city
    current_city = cities[0]
    path.append(current_city)
    visited[cities.index(current_city)] = True
    
    # Repeat until all cities are visited
    while len(path) < n:
        nearest_city = None
        nearest_distance = float('inf')
        
        # Find the nearest unvisited city
        for city in cities:
            if not visited[cities.index(city)] and (((current_city, city) in distances) | ((city, current_city) in distances)):
                try:
                    distance = distances[(current_city, city)]
                except KeyError:
                    distance = distances[(city, current_city)]
                if distance < nearest_distance:
                    nearest_distance = distance
                    nearest_city = city
        
        # Move to the nearest city
        total_distance += nearest_distance
        current_city = nearest_city

        path.append(current_city)

        try:
            visited[cities.index(current_city)] = True
        except ValueError:
            ipdb.set_trace()
    
    # Return to the starting city
    total_distance += distances.get((current_city, path[0]), distances.get((path[0], current_city)))
    path.append(path[0])
    
    return path, total_distance

In [ ]:

# Apply nearest neighbor algorithm
path, total_distance = nearest_neighbor(mx_driving_distance, 'Mexico City, Mexico')

# Print the result
print("Nearest Neighbor Path:", path)
print("Total Distance:", total_distance)

## Minimum spanning tree

In [12]:
import networkx as nx
from tqdm import tqdm

In [ ]:
mx_driving_distance

In [31]:
def mst(data):
    
    G = nx.Graph()

    mat = []

    for k, v in data.items():
        mat.append((k[0], k[1], {"weight": v}))

    G.add_edges_from(mat)
    T = nx.minimum_spanning_tree(G)

    return T

def plot_map(T):
    locations = []

    m = folium.Map()
    my_edges = list(T.edges)
    
    for pairs in tqdm(my_edges):
    
        locations = []
    
        city_1 = pairs[0]
        city_2 = pairs[1]
        tmp = list(filter(lambda x: ((x["city_1"] == city_1) & (x["city_2"] == city_2)) | 
                          ((x["city_1"] == city_2) & (x["city_2"] == city_1)), data))
        
        try:
            for loc_data in tmp[0]['driving_leg'][0]['steps']:
                locations.extend(decode_polyline(loc_data['polyline']['points']))
        except IndexError:
            continue
            
        folium.Marker(
            location=locations[0],
            popup=folium.Popup(city_1, parse_html=True, max_width=100),
        ).add_to(m)
    
        folium.Marker(
            location=locations[-1],
            popup=folium.Popup(city_2, parse_html=True, max_width=100),
        ).add_to(m)
        folium.PolyLine(locations, tooltip="Coast").add_to(m)

    return m

In [32]:
T_mx = mst(mx_driving_distance)

In [33]:
map_mx = plot_map(T_mx)

100%|█████████████████████████████████████| 16/16 [00:00<00:00, 81.53it/s]


In [34]:
map_mx

In [35]:
T_full = mst(driving_distance)

In [36]:
map_full = plot_map(T_full)

100%|████████████████████████████████████| 50/50 [00:00<00:00, 147.03it/s]


In [37]:
map_full

In [5]:
mx_data = list(filter(lambda x: ("Mexico" in x['city_1']) & ("Mexico" in x['city_2']), data))

In [36]:
tmp_list = ["Oaxaca, Mexico", "Mexico City, Mexico", "Merida, Mexico"]

In [37]:
mx_data = list(filter(lambda x: (x['city_1'] in tmp_list) | (x['city_2'] in tmp_list), data))

In [35]:
mx_data = list(filter(lambda x: tmp_list[0] in x["city_1"], data))

In [25]:
tmp_list

['Oaxaca', 'Mexico City', 'Merida']

In [39]:
len(mx_data)

147

In [27]:
data[0]["city_1"]

'Mexico City, Mexico'